In [ ]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
%%time

%cd /content/
%rm -rf LLaMA-Factory
!git clone https://github.com/hiyouga/LLaMA-Factory.git
%cd LLaMA-Factory
%ls
!pip install -e .[torch,bitsandbytes]
# Installs Unsloth, Xformers (Flash Attention) and all other packages!
!pip install "unsloth[colab-new] @ git+https://github.com/unslothai/unsloth.git"
!pip install --no-deps xformers "trl<0.9.0" peft accelerate bitsandbytes

/content
Cloning into 'LLaMA-Factory'...
remote: Enumerating objects: 15281, done.
remote: Counting objects: 100% (231/231), done.
remote: Compressing objects: 100% (97/97), done.
remote: Total 15281 (delta 141), reused 193 (delta 133), pack-reused 15050
Receiving objects: 100% (15281/15281), 221.47 MiB | 21.94 MiB/s, done.
Resolving deltas: 100% (11174/11174), done.
/content/LLaMA-Factory
assets/       docker/      LICENSE      pyproject.toml  requirements.txt  src/
CITATION.cff  evaluation/  Makefile     README.md       scripts/          tests/
data/         examples/    MANIFEST.in  README_zh.md    setup.py
Obtaining file:///content/LLaMA-Factory
  Installing build dependencies ... done
  Checking if build backend supports build_editable ... done
  Getting requirements to build editable ... done
  Preparing editable metadata (pyproject.toml) ... done
  Building editable for llamafactory (pyproject.toml) ... done
  Created wheel for llamafactory: filename=llamafactory-0.8.3.dev0-0.ed

In [ ]:
import os
import sys
from pathlib import Path

workding_dir = "/content/drive/MyDrive/logical-reasoning/"
os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /content/drive/MyDrive/logical-reasoning/


In [ ]:
need_to_setup_env = True
need_to_setup_env

True

In [ ]:
if need_to_setup_env:
    %pip install -r requirements.txt

In [ ]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /content/drive/.shortcut-targets-by-id/1E09lTnfbsjtTgQg65dQ3y9D2R6l8waxR/logical-reasoning/.env


True

In [ ]:
import os

model_name = os.getenv("MODEL_NAME")
token = os.getenv("HF_TOKEN") or None
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
local_model = os.getenv("LOCAL_MODEL")
hub_model = os.getenv("HUB_MODEL")
num_train_epochs = int(os.getenv("NUM_TRAIN_EPOCHS") or 0)
data_path = os.getenv("LOGICAL_REASONING_DATA_PATH")
results_path = os.getenv("LOGICAL_REASONING_RESULTS_PATH")

max_seq_length = 2048  # Choose any! We auto support RoPE Scaling internally!
dtype = (
    None  # None for auto detection. Float16 for Tesla T4, V100, Bfloat16 for Ampere+
)

model_name, load_in_4bit, local_model, hub_model, max_seq_length, num_train_epochs, dtype, data_path, results_path, os.getenv("DISABLE_MLFLOW_INTEGRATION"), os.getenv("WANDB_DISABLED")

('Qwen2/Qwen2-7B-Instruct',
 True,
 None,
 None,
 2048,
 6,
 None,
 'datasets/mgtv',
 'results/mgtv-results_colab.csv',
 None,
 None)

In [ ]:
!nvidia-smi

Sun Jul  7 06:05:25 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  Tesla T4                       Off | 00000000:00:04.0 Off |                    0 |
| N/A   46C    P8               9W /  70W |      0MiB / 15360MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [ ]:
%%time
!python --version
!pip show flash-attn

Python 3.10.12
CPU times: user 11.4 ms, sys: 2.65 ms, total: 14 ms
Wall time: 711 ms


In [ ]:
def evaluate_model_all_epochs(model_name, num_train_epochs, adapter_path_base, load_in_4bit=True, use_english_datasets=False, num_of_entries=-1):
    os.environ["MODEL_NAME"] = model_name
    os.environ["LOAD_IN_4BIT"] = "true" if load_in_4bit else "false"
    os.environ["USE_ENGLISH_DATASETS"] = "true" if use_english_datasets else "false"
    for i in range(num_train_epochs + 1):
        print(f"Epoch {i}")
        if i == 0:
            os.unsetenv("ADAPTER_NAME_OR_PATH")
        else:
            adapter_path = f"{adapter_path_base}/checkpoint-{560 * i}"
            os.environ["ADAPTER_NAME_OR_PATH"] = adapter_path

        !python llm_toolkit/eval_logical_reasoning.py {num_of_entries}

In [ ]:
%%time

evaluate_model_all_epochs("gradientai/Llama-3-8B-Instruct-Gradient-1048k", 0, "", load_in_4bit=False, use_english_datasets=True, num_of_entries=5)

Epoch 0
loading env vars from: /content/drive/.shortcut-targets-by-id/1E09lTnfbsjtTgQg65dQ3y9D2R6l8waxR/logical-reasoning/.env
Adding /content/drive/.shortcut-targets-by-id/1E09lTnfbsjtTgQg65dQ3y9D2R6l8waxR/logical-reasoning to sys.path
2024-07-07 06:50:11.960720: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-07-07 06:50:11.960772: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-07-07 06:50:11.968499: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-07-07 06:50:11.988300: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use avai